In [1]:
import pandas as pd
import hail as hl
hl.init()

Running on Apache Spark version 2.4.5
SparkUI available at http://hailtest2-m.us-central1-b.c.cncd-cncd.internal:4041
Welcome to
     __  __     <>__
    / /_/ /__  __/ /
   / __  / _ `/ / /
  /_/ /_/\_,_/_/_/   version 0.2.59-63cf625e29e5
LOGGING: writing to /hail-20201130-0905-0.2.59-63cf625e29e5.log


In [2]:
!rm *.xlsx

rm: cannot remove '*.xlsx': No such file or directory


In [ ]:
for chro in list(range(1,23))+['X','Y']:
    try:#pgr-wgs-8k/VEP_VCF/pgr8k_chr1_VEP.mt
        print("Reading Data")
        data = hl.read_matrix_table("gs://pgr-wgs-2k/VEP_VCF/Chr" + str(chro) + "_2k_wgs.mt")
        print("Filtering Transcripts")        
#         canonical = data.vep.transcript_consequences.filter(lambda csq: csq.canonical == 1)
#         data = data.annotate_rows(canonical_transcript=canonical)
        data = data.filter_rows(data.variant_qc.AF[1] < 0.05)

        data = data.filter_rows( ( data.vep.most_severe_consequence ==  'missense_variant' ) )
#         data = data.filter_rows(hl.len(data.canonical_transcript.exon) != 0)
#         data.canonical_transcript.exon.show()
        print(data.count())
#         print("Annotating DB")
#         db = hl.experimental.DB()
#         data = db.annotate_rows_db(data, 'clinvar_variant_summary','dbNSFP_genes','dbNSFP_variants','gnomad_exome_sites')
#         data.rows().show()
        print("Saving to Disk")
#         data.write("gs://pgr-wgs-8k/Complete_Annotations/Canonical/8K_Chr"+str(chro)+"_VEP_DB_C.mt", overwrite=True)


        print('Annotate Heterozygous Alleles')
        ds_result1 = data.annotate_rows(hets = hl.agg.filter(data.GT.is_het(),hl.agg.collect(data.s)))
        ds_result1.count()
        print('Annotate N Hets')
        ds_result4 = ds_result1.annotate_rows(n_het = hl.agg.count_where(ds_result1.GT.is_het()))
        ds_result4.count()
        print('Annotate Homozygous Alleles')
        ds_result3 = ds_result4.annotate_rows(homs = hl.agg.filter(ds_result4.GT.is_hom_var(),hl.agg.collect(ds_result4.s)))
        ds_result3.count()
        print('Annotating N Homs')
        ds_result5 = ds_result3.annotate_rows(n_hom = hl.agg.count_where(ds_result3.GT.is_hom_var()))
        ds_result5.count()
        ds_result5.rows().show()

        print('Selecting Data To Query')
        ds_result6 = ds_result5.rows()
        ds_result6 = ds_result6.key_by()

        print('Converting To Pandas')
        finData_All = ds_result6.select(
            locus=ds_result6.locus,
            alleles=ds_result6.alleles,
            gene=ds_result6.canonical_transcript.gene_symbol,
            lof=ds_result6.canonical_transcript.lof,
            maf=ds_result6.variant_qc.AF[1],
            consequence=ds_result6.vep.most_severe_consequence,
            hets=ds_result6.hets,
            n_hets=ds_result6.n_het,
            homs=ds_result6.homs,
            n_homs=ds_result6.n_hom
        ).to_pandas()      

        finData_All.to_excel("Chr"+str(chro)+"_2k.xlsx")
        !gsutil -m cp *.xlsx gs://pgr-wgs-2k/Complete_Annotations/Missense/
        !rm *.xlsx
        print("Done")
        
    except:
        print("Error in Chr", chro)

Reading Data
Filtering Transcripts


+---------------+----------------+------------+
| locus         | alleles        | <expr>     |
+---------------+----------------+------------+
| locus<GRCh38> | array<str>     | array<str> |
+---------------+----------------+------------+
| chr1:69159    | ["G","GT"]     | ["1/1"]    |
| chr1:69159    | ["GT","G"]     | ["1/1"]    |
| chr1:69336    | ["CAA","C"]    | ["1/1"]    |
| chr1:69337    | ["A","T"]      | ["1/1"]    |
| chr1:69469    | ["ACAATT","A"] | ["1/1"]    |
| chr1:69702    | ["TG","T"]     | ["1/1"]    |
| chr1:69745    | ["C","CA"]     | ["1/1"]    |
| chr1:69745    | ["C","T"]      | ["1/1"]    |
| chr1:69849    | ["G","A"]      | ["1/1"]    |
| chr1:69869    | ["T","A"]      | ["1/1"]    |
+---------------+----------------+------------+
showing top 10 rows

(50972, 7482)
Saving to Disk
Annotate Heterozygous Alleles
Annotate N Hets
Annotate Homozygous Alleles
Annotating N Homs


+---------------+----------------+----------------+----------+
| locus         | alleles        | rsid           |     qual |
+---------------+----------------+----------------+----------+
| locus<GRCh38> | array<str>     | str            |  float64 |
+---------------+----------------+----------------+----------+
| chr1:69159    | ["G","GT"]     | "rs1200057930" | 3.40e+01 |
| chr1:69159    | ["GT","G"]     | NA             | 3.20e+01 |
| chr1:69336    | ["CAA","C"]    | NA             | 5.00e+00 |
| chr1:69337    | ["A","T"]      | NA             | 3.10e+01 |
| chr1:69469    | ["ACAATT","A"] | "rs1350212330" | 3.20e+01 |
| chr1:69702    | ["TG","T"]     | "rs1326619681" | 7.50e+01 |
| chr1:69745    | ["C","CA"]     | "rs774480782"  | 7.10e+01 |
| chr1:69745    | ["C","T"]      | "rs1308429174" | 2.55e+02 |
| chr1:69849    | ["G","A"]      | "rs776815449"  | 2.55e+02 |
| chr1:69869    | ["T","A"]      | "rs548049170"  | 2.55e+02 |
+---------------+----------------+----------------+----------+

+------------------------------+------------+--------------+---------+
| filters                      | info.AVGDP | info.AC      | info.AN |
+------------------------------+------------+--------------+---------+
| set<str>                     |    float64 | array<int32> |   int32 |
+------------------------------+------------+--------------+---------+
| {"SVM","MIS2"}               |   8.10e+00 | [0]          |    3006 |
| {"MIS2"}                     |   8.10e+00 | [0]          |    3006 |
| {"SVM","MIS2"}               |   8.38e+00 | [0]          |    6470 |
| {"MIS2"}                     |   8.51e+00 | [0]          |    6562 |
| {"MIS2"}                     |   1.49e+01 | [0]          |   10322 |
| {"SVM","MIS2"}               |   1.10e+01 | [0]          |    7976 |
| {"SVM","MIS2"}               |   1.29e+01 | [0]          |    7898 |
| {"SVM","DUP2","TRI2","MIS2"} |   1.29e+01 | [0]          |    7898 |
| {"SVM","DUP2","TRI2","MIS2"} |   1.23e+01 | [230]        |    5994 |
| {"SVM","MIS2"}               |   1.23e+01 | [4]          |    6082 |
+------------------------------+------------+--------------+---------+

+-------------+----------------+-------------+----------------+-------------+
| info.FIBC_P | info.HWE_SLP_P | info.FIBC_I | info.HWE_SLP_I | info.MAX_IF |
+-------------+----------------+-------------+----------------+-------------+
|     float64 |        float64 |     float64 |        float64 |     float64 |
+-------------+----------------+-------------+----------------+-------------+
|    5.01e-01 |       3.83e-06 |    5.01e-01 |       3.83e-06 |    1.00e-05 |
|    5.06e-01 |       2.21e-04 |    5.06e-01 |       2.21e-04 |    1.00e-05 |
|    4.68e-01 |       1.24e-01 |    4.68e-01 |       1.24e-01 |    1.00e-05 |
|    4.09e-01 |       1.12e-04 |    4.40e-01 |       1.12e-04 |    1.53e-04 |
|    4.18e-01 |       2.20e-04 |    4.18e-01 |       2.20e-04 |    1.00e-05 |
|    5.54e-01 |       3.52e-06 |    5.54e-01 |       3.52e-06 |    1.00e-05 |
|    8.77e-02 |       1.03e-04 |    2.74e-01 |       1.06e-04 |    2.08e-05 |
|    1.25e-03 |       3.80e-01 |   -9.50e-04 |      -1.39e-01 |    1.79e-02 |
|    1.24e-03 |       4.12e-01 |   -6.65e-02 |      -3.81e+00 |    3.62e-01 |
|    6.73e-02 |       3.34e+00 |    8.38e-02 |       3.31e+00 |    9.39e-04 |
+-------------+----------------+-------------+----------------+-------------+

+-------------+------------------------------------------------------------+
| info.MIN_IF | info.BETA_IF                                               |
+-------------+------------------------------------------------------------+
|     float64 | array<float64>                                             |
+-------------+------------------------------------------------------------+
|    1.00e-05 | [2.36e-06,6.47e-05,8.42e-05,1.82e-05,1.25e-04,1.00e+00]    |
|    1.00e-05 | [2.66e-06,5.72e-05,7.78e-05,2.08e-05,7.00e-05,1.00e+00]    |
|    1.00e-05 | [3.76e-06,7.16e-05,9.96e-05,6.15e-06,1.63e-04,1.00

Selecting Data To Query
Converting To Pandas
Copying file://Chr1_8k.xlsx [Content-Type=application/vnd.openxmlformats-officedocument.spreadsheetml.sheet]...
/ [1/1 files][  2.5 MiB/  2.5 MiB] 100% Done                                    
Operation completed over 1 objects/2.5 MiB.                                      
Done
Reading Data
Filtering Transcripts


...

Selecting Data To Query
Converting To Pandas
Copying file://Chr21_8k.xlsx [Content-Type=application/vnd.openxmlformats-officedocument.spreadsheetml.sheet]...
/ [1/1 files][243.5 KiB/243.5 KiB] 100% Done                                    
Operation completed over 1 objects/243.5 KiB.                                    
Done
Reading Data
Filtering Transcripts


+----------------+-------------+------------+
| locus          | alleles     | <expr>     |
+----------------+-------------+------------+
| locus<GRCh38>  | array<str>  | array<str> |
+----------------+-------------+------------+
| chr22:15528177 | ["C","T"]   | ["1/1"]    |
| chr22:15528234 | ["G","T"]   | ["1/1"]    |
| chr22:15528236 | ["AT","A"]  | ["1/1"]    |
| chr22:15528246 | ["C","T"]   | ["1/1"]    |
| chr22:15528257 | ["T","TTG"] | ["1/1"]    |
| chr22:15528260 | ["T","A"]   | ["1/1"]    |
| chr22:15528265 | ["G","A"]   | ["1/1"]    |
| chr22:15528270 | ["AT","A"]  | ["1/1"]    |
| chr22:15528352 | ["G","A"]   | ["1/1"]    |
| chr22:15528363 | ["C","T"]   | ["1/1"]    |
+----------------+-------------+------------+
showing top 10 rows

(10680, 7482)
Saving to Disk
Annotate Heterozygous Alleles
Annotate N Hets
Annotate Homozygous Alleles
Annotating N Homs


+----------------+-------------+----------------+----------+
| locus          | alleles     | rsid           |     qual |
+----------------+-------------+----------------+----------+
| locus<GRCh38>  | array<str>  | str            |  float64 |
+----------------+-------------+----------------+----------+
| chr22:15528177 | ["C","T"]   | "rs780256539"  | 2.55e+02 |
| chr22:15528234 | ["G","T"]   | "rs1420478920" | 4.30e+01 |
| chr22:15528236 | ["AT","A"]  | "rs1251396180" | 9.50e+01 |
| chr22:15528246 | ["C","T"]   | "rs751806421"  | 1.03e+02 |
| chr22:15528257 | ["T","TTG"] | NA             | 4.40e+01 |
| chr22:15528260 | ["T","A"]   | "rs1243387448" | 2.55e+02 |
| chr22:15528265 | ["G","A"]   | "rs1308943530" | 9.50e+01 |
| chr22:15528270 | ["AT","A"]  | "rs757403607"  | 4.10e+01 |
| chr22:15528352 | ["G","A"]   | "rs571475163"  | 7.90e+01 |
| chr22:15528363 | ["C","T"]   | "rs200937709"  | 2.55e+02 |
+----------------+-------------+----------------+----------+

+-----------------------+------------+--------------+---------+-------------+
| filters               | info.AVGDP | info.AC      | info.AN | info.FIBC_P |
+-----------------------+------------+--------------+---------+-------------+
| set<str>              |    float64 | array<int32> |   int32 |     float64 |
+-----------------------+------------+--------------+---------+-------------+
| {"SVM","DUP2","TRI2"} |   4.47e+01 | [95]         |   14964 |   -5.20e-04 |
| {}                    |   5.67e+01 | [0]          |   14964 |    4.87e-01 |
| {"SVM"}               |   5.74e+01 | [0]          |   14964 |    5.47e-01 |
| {}                    |   6.04e+01 | [0]          |   14964 |    6.65e-01 |
| {}                    |   6.35e+01 | [0]          |   14964 |    6.65e-01 |
| {"SVM"}               |   6.40e+01 | [0]          |   14964 |   -8.56e-06 |
| {"SVM"}               |   6.44e+01 | [0]          |   14964 |   -1.14e-05 |
| {}                    |   6.47e+01 | [0]          |   14964 |    6.65e-01 |
| {"SVM"}               |   6.65e+01 | [0]          |   14958 |    1.74e-01 |
| {"SVM"}               |   6.56e+01 | [1]          |   14960 |   -2.08e-04 |
+-----------------------+------------+--------------+---------+-------------+

+----------------+-------------+----------------+-------------+-------------+
| info.HWE_SLP_P | info.FIBC_I | info.HWE_SLP_I | info.MAX_IF | info.MIN_IF |
+----------------+-------------+----------------+-------------+-------------+
|        float64 |     float64 |        float64 |     float64 |     float64 |
+----------------+-------------+----------------+-------------+-------------+
|      -2.41e-02 |    2.87e-02 |      -2.38e-02 |    1.60e-02 |    1.00e-05 |
|       1.47e-06 |    4.89e-01 |       1.51e-06 |    3.85e-05 |    1.00e-05 |
|       2.70e-06 |    5.90e-01 |       4.77e-06 |    2.39e-04 |    1.00e-05 |
|       5.14e-06 |    6.65e-01 |       5.14e-06 |    1.00e-05 |    1.00e-05 |
|       5.14e-06 |    7.06e-01 |       6.58e-06 |    7.91e-05 |    1.00e-05 |
|      -9.04e-06 |    1.13e-01 |      -7.69e-06 |    1.54e-05 |    1.00e-05 |
|      -1.49e-05 |    7.22e-02 |      -1.34e-05 |    6.93e-05 |    1.00e-05 |
|       5.14e-06 |    6.65e-01 |       5.14e-06 |    1.00e-05 |    1.00e-05 |
|      -5.00e-06 |    4.04e-01 |      -1.06e-06 |    3.61e-05 |    1.00e-05 |
|      -3.80e-03 |    7.33e-03 |      -3.78e-03 |    3.12e-04 |    1.00e-05 |
+----------------+-------------+----------------+-------------+-------------+

+-------------------------------------------------------------+----------+
| info.BETA_IF                                                | info.ABE |
+-------------------------------------------------------------+----------+
| array<float64>                                              |  float64 |
+-------------------------------------------------------------+----------+
| [1.35e-03,-1.17e-02,-1.03e-04,1.39e-02,-1.42e-01,1.00e+00]  | 7.43e-01 |
| [4.42e-06,8.77e-05,1.07e-04,1.35e-04,-3.45e-04,1.00e+00]    | 7.65e-01 |


Selecting Data To Query
Converting To Pandas
Copying file://Chr22_8k.xlsx [Content-Type=application/vnd.openxmlformats-officedocument.spreadsheetml.sheet]...
/ [1/1 files][539.3 KiB/539.3 KiB] 100% Done                                    
Operation completed over 1 objects/539.3 KiB.                                    
Done
Reading Data
Error in Chr X
Reading Data
Error in Chr Y


In [ ]:
data.canonical_transcript.lof.show(10000)

In [ ]:
data2 = hl.read_matrix_table("gs://pgr-wgs-8k/VEP_VCF/pgr8k_chr21_VEP.mt")
data2.rows().show(1)

In [ ]:
data2.vep.transcript_consequences[0].exon.show(500)

In [ ]:
chro = 12
bp = 112036778

data = hl.read_matrix_table("gs://pgr-wes-30k-mt/Vep_MT/Promis30_chr"+str(chro)+"_VEP.mt")
data1 = data.filter_rows(data.locus == hl.parse_locus( str(chro)+':'+str(bp) ) )
data1.rows().show()

In [ ]:
data1= hl.split_multi_hts(data1)
print('Annotate Heterozygous Alleles')
ds_result1 = data1.annotate_rows(hets = hl.agg.filter(data1.GT.is_het(),hl.agg.collect(data1.s)))
ds_result1.count()
print('Annotate N Hets')
ds_result4 = ds_result1.annotate_rows(n_het = hl.agg.count_where(ds_result1.GT.is_het()))
ds_result4.count()
print('Annotate Homozygous Alleles')
ds_result3 = ds_result4.annotate_rows(homs = hl.agg.filter(ds_result4.GT.is_hom_var(),hl.agg.collect(ds_result4.s)))
ds_result3.count()
print('Annotating N Homs')
ds_result5 = ds_result3.annotate_rows(n_hom = hl.agg.count_where(ds_result3.GT.is_hom_var()))
ds_result5.count()
ds_result5.rows().show()

print('Selecting Data To Query')
ds_result6 = ds_result5.rows()
ds_result6 = ds_result6.key_by()

print('Converting To Pandas')
finData_All = ds_result6.select(
    locus=ds_result6.locus,
    alleles=ds_result6.alleles,
    gene=ds_result6.vep.transcript_consequences.gene_symbol,
    lof=ds_result6.vep.transcript_consequences.lof,
    consequence=ds_result6.vep.most_severe_consequence,
    hets=ds_result6.hets,
    n_hets=ds_result6.n_het,
    homs=ds_result6.homs,
    n_homs=ds_result6.n_hom
).to_pandas()      

finData_All.to_excel("Chr"+str(chro)+":"+str(bp)+".xlsx")
print("Done")

In [ ]:
!ls
!gsutil -m cp *.xlsx gs://pgr-wes-30k-mt/Salman

In [ ]:

for chro in [3,5,7,8,17,18,19,20]:#range(1,23):
     try:
        print('Importing Data', str(chro))
        data2 = hl.read_matrix_table("gs://pgr-wes-r20/VEP/Chr" + str(chro) + "_r20_VEP.mt")
        data2.rows().show()
        data2= hl.split_multi_hts(data2)
        print('DONE MAV')
        print(data2.count())
        print('Filtering Minor Allele Frequency')
        data2 = hl.variant_qc(data2)
        data2 = data2.filter_rows(data2.variant_qc.AF[1] < 0.05)
        print(data2.count())
        
        print('Filtering LOF & Missense')
    #     table_hc = data2.filter_rows(data2.vep.intergenic_consequences[0].consequence_terms[0] == 'missense')
        table_hc = data2.filter_rows((data2.vep.most_severe_consequence == 'missense_variant') | (data2.vep.transcript_consequences.lof.contains('HC' ) ))
    #     print(table_hc.count())
        print(table_hc.count())

        print('Annotate Heterozygous Alleles')
        ds_result1 = table_hc.annotate_rows(hets = hl.agg.filter(table_hc.GT.is_het(),hl.agg.collect(table_hc.s)))
        ds_result1.count()
        print('Annotate N Hets')
        ds_result4 = ds_result1.annotate_rows(n_het = hl.agg.count_where(ds_result1.GT.is_het()))
        ds_result4.count()
        print('Annotate Homozygous Alleles')
        ds_result3 = ds_result4.annotate_rows(homs = hl.agg.filter(ds_result4.GT.is_hom_var(),hl.agg.collect(ds_result4.s)))
        ds_result3.count()
        print('Annotating N Homs')
        ds_result5 = ds_result3.annotate_rows(n_hom = hl.agg.count_where(ds_result3.GT.is_hom_var()))
        ds_result5.count()

        print('Selecting Data To Query')
        ds_result6 = ds_result5.rows()
        ds_result6 = ds_result6.key_by()

        print('Converting To Pandas')
        finData_All = ds_result6.select(
            locus=ds_result6.locus,
            alleles=ds_result6.alleles,
            gene=ds_result6.vep.transcript_consequences.gene_symbol,
            lof=ds_result6.vep.transcript_consequences.lof,
            consequence=ds_result6.vep.most_severe_consequence,
    #         AF=ds_result6.info.AF,
            hets=ds_result6.hets,
            n_hets=ds_result6.n_het,
            homs=ds_result6.homs,
            n_homs=ds_result6.n_hom
    #         amino_acids=ds_result6.vep.transcript_consequences[0].amino_acids,
    #         exon=ds_result6.vep.transcript_consequences[0].exon,    
    #         polyphen_prediction=ds_result6.vep.transcript_consequences[0].polyphen_prediction,
    #         polyphen_score=ds_result6.vep.transcript_consequences[0].polyphen_score,
    #         sift_prediction=ds_result6.vep.transcript_consequences[0].sift_prediction,
    #         sift_score=ds_result6.vep.transcript_consequences[0].sift_score,
    #         clinvar_signif=ds_result6.dbNSFP_variants.clinvar_clnsig,
    #         clinvar_trait=ds_result6.dbNSFP_variants.clinvar_trait,
    #         clinvar_MedGen_id=ds_result6.dbNSFP_variants.clinvar_MedGen_id,
    #         REVEL_score=ds_result6.dbNSFP_variants.REVEL_score,
    #         REVEL_rankscore=ds_result6.dbNSFP_variants.REVEL_rankscore,
    #         MutationTaster_pred=ds_result6.dbNSFP_variants.MutationTaster_pred,
    #         LRT_pred=ds_result6.dbNSFP_variants.LRT_pred,
    #         Polyphen2_HVAR_pred=ds_result6.dbNSFP_variants.Polyphen2_HVAR_pred,
    #         Polyphen2_HDIV_pred=ds_result6.dbNSFP_variants.Polyphen2_HDIV_pred,
    #         CADD_phred=ds_result6.dbNSFP_variants.CADD_phred,
    #         DANN_score=ds_result6.dbNSFP_variants.DANN_score
        ).to_pandas()       

        finData_All.to_excel('Chr'+str(chro)+'_r20.xlsx', index=False)
        finData_All = pd.read_excel('Chr'+str(chro)+'_r20.xlsx')
        !rm *.xlsx
#         print(finData_All.head())
#         print("Formatting Excel")
        new = finData_All['gene'].str.split("'", expand = True)
#         new[1]
        finData_All["gene_symbol"] = new[1]

        new1 = finData_All['lof'].str.split("'", expand = True)
#         new1[1]
        finData_All["Lof"] = new1[1]
        
        finData_All.drop(['gene', 'lof'], axis=1, inplace=True)
        
        
        #For HC
        finData_All1 = finData_All[finData_All['Lof'] == 'HC']       
        print(finData_All1.shape)
        print("Saving Excel HC")
        finData_All1.to_excel('Chr'+str(chro)+'_30k_targets_HC.xlsx', index=False)
        !gsutil -m cp *.xlsx gs://pgr-wes-r20/Excel_Output/Targets/HC/
        !rm *.xlsx
        dfLC1 = finData_All1.sort_values('gene_symbol')
        print("Printing DF")
        print(dfLC1.head())
        dfHetHom1 = dfLC1[['gene_symbol', 'hets', 'homs']]
        dfNHetHoms1 = dfLC1[['gene_symbol', 'n_hets', 'n_homs']]
        dfHetHom1 = dfHetHom1.groupby('gene_symbol').aggregate(lambda tdf: tdf.tolist())
        print(dfHetHom1.shape)
        dfNHetHoms1 = dfNHetHoms1.groupby('gene_symbol').agg(sum)
        print(dfNHetHoms1.shape)
        concatenated_lc = pd.concat([dfHetHom1, dfNHetHoms1], axis=1)
        print(concatenated_lc.shape)
        concatenated_lc.to_excel('Chr'+str(chro)+'_30k_KO_HC.xlsx', index=True)
        !gsutil -m cp *.xlsx gs://pgr-wes-r20/Excel_Output/Knockouts/HC/
        !rm *.xlsx
        
        #For Missense
        finData_All1 = finData_All[finData_All['consequence'] == 'missense_variant']    
        print(finData_All1.shape)
        print("Saving Excel Missense")
        finData_All1.to_excel('Chr'+str(chro)+'_30k_targets_Missense.xlsx', index=False)
        !gsutil -m cp *.xlsx gs://pgr-wes-r20/Excel_Output/Targets/Missense/
        !rm *.xlsx
        dfLC1 = finData_All1.sort_values('gene_symbol')
        print("Printing DF")
        print(dfLC1.head())
        dfHetHom1 = dfLC1[['gene_symbol', 'hets', 'homs']]
        dfNHetHoms1 = dfLC1[['gene_symbol', 'n_hets', 'n_homs']]
        dfHetHom1 = dfHetHom1.groupby('gene_symbol').aggregate(lambda tdf: tdf.tolist())
        print(dfHetHom1.shape)
        dfNHetHoms1 = dfNHetHoms1.groupby('gene_symbol').agg(sum)
        print(dfNHetHoms1.shape)
        concatenated_lc = pd.concat([dfHetHom1, dfNHetHoms1], axis=1)
        print(concatenated_lc.shape)
        concatenated_lc.to_excel('Chr'+str(chro)+'_30k_KO_Missense.xlsx', index=True)
        !gsutil -m cp *.xlsx gs://pgr-wes-r20/Excel_Output/Knockouts/Missense/
        !rm *.xlsx
        print('Complete')
        

     except Exception as e: print(e) 